#Get Dataset From Kaggle

In [ ]:
%%bash 
pip uninstall -y kaggle 
pip install --upgrade pip 
pip install kaggle==1.5.6 
kaggle -v 
mkdir -p ~/.kaggle/ && mv kaggle.json ~/.kaggle/ && chmod 600 ~/.kaggle/kaggle.json
kaggle competitions download -c tensorflow-speech-recognition-challenge
unzip /content/tensorflow-speech-recognition-challenge.zip

Uninstalling kaggle-1.5.12:
  Successfully uninstalled kaggle-1.5.12
  Found existing installation: pip 19.3.1
    Uninstalling pip-19.3.1:
      Successfully uninstalled pip-19.3.1
  Created wheel for kaggle: filename=kaggle-1.5.6-py3-none-any.whl size=72859 sha256=18c74ce1a800ca4806c48f2583ba52be3d3bd40b7acd023accddf739037fb167
  Stored in directory: /root/.cache/pip/wheels/aa/e7/e7/eb3c3d514c33294d77ddd5a856bdd58dc9c1fabbed59a02a2b
Successfully built kaggle

Archive:  /content/tensorflow-speech-recognition-challenge.zip
  inflating: link_to_gcp_credits_form.txt  
  inflating: sample_submission.7z    
  inflating: test.7z                 
  inflating: train.7z                


Traceback (most recent call last):
  File "/usr/local/bin/kaggle", line 5, in <module>
    from kaggle.cli import main
  File "/usr/local/lib/python3.7/dist-packages/kaggle/__init__.py", line 23, in <module>
    api.authenticate()
  File "/usr/local/lib/python3.7/dist-packages/kaggle/api/kaggle_api_extended.py", line 149, in authenticate
    self.config_file, self.config_dir))
OSError: Could not find kaggle.json. Make sure it's located in /root/.kaggle. Or use the environment method.
100%|██████████| 3.50G/3.50G [00:42<00:00, 89.1MB/s]


#Unzip Test File

Using `p7zip` in the command line, I unzip the test file. 

In [ ]:
!p7zip -d test.7z


7-Zip (a) [64] 16.02 : Copyright (c) 1999-2016 Igor Pavlov : 2016-05-21
p7zip Version 16.02 (locale=en_US.UTF-8,Utf16=on,HugeFiles=on,64 bits,2 CPUs Intel(R) Xeon(R) CPU @ 2.00GHz (50653),ASM,AES-NI)

Scanning the drive for archives:
  0M Scan         1 file, 2640679130 bytes (2519 MiB)

Extracting archive: test.7z
--
Path = test.7z
Type = 7z
Physical Size = 2640679130
Headers Size = 1345163
Method = Delta LZMA2:24
Solid = +
Blocks = 3

  0%      0% 117          0% 263 - test/audio/clip_006bd0d1c.wav                                          0% 394 - test/audio/clip_00a6a6702.wav                                          0% 530 - test/audio/clip_00ea22146.wav                                          0% 657 - t

I then check if the number of files unzipped from the test folder is the same as described in the Kaggle task. 

In [ ]:
test_audio = '/content/test/audio'
examples = [os.path.join(test_audio, f) for f in os.listdir(test_audio)] #check this path to make sure it goes to the audio 

Since, the length of examples is the same as prescribed in Kaggle, I can assume that the dataset is fully intact. 

In [ ]:
len(examples)

158538

#Load Libraries

In [ ]:
import os 
import librosa
import librosa.display
import matplotlib.pyplot as plt
import re
import numpy as np 
from matplotlib.backends.backend_agg import FigureCanvasAgg as FigureCanvas

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


#Spectogram Images

In [ ]:
def spectogram_test(examples):
  hop_length = 512
  n_fft = 512 #suggested for speech
  os.makedirs('test_spec', exist_ok = True)
  spec_images = '/content/test_spec'

  for idx,ex in enumerate(examples): 
    if idx%1000 == 0: print(idx)
    fig = plt.Figure()
    canvas = FigureCanvas(fig)
    ax = fig.add_subplot(111)
    
    name = re.findall(r'[\w]+.wav',ex)[0]
    clip, sample_rate = librosa.load(ex)

    spec = librosa.amplitude_to_db(np.abs(librosa.stft(clip, hop_length=hop_length, n_fft = n_fft)), ref=np.max)
    p = librosa.display.specshow(spec, y_axis=None, sr=sample_rate, ax = ax,hop_length=hop_length, x_axis=None)
    fig.savefig(f'{spec_images}/{name[:-3]}jpg')

spectogram_test(examples)

0
1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000
92000
93000
94000
95000
96000
97000
98000
99000
100000
101000
102000
103000
104000
105000
106000
107000
108000
109000
110000
111000
112000
113000
114000
115000
116000
117000
118000
119000
120000
121000
122000
123000
124000
125000
126000
127000
128000
129000
130000
131000
132000
133000
134000
135000
136000
137000
138000
139000
140000
141000
142000
143000
144000
145000
146000
147000
148000
149000
150000
151000
152000
153000
154000
155000
156000
157000
158000


In [ ]:
%%bash
#zip -r /content/test_spec.zip /content/test_spec
rm -r test_spec

##Upload 
Upload the `test_spec` images to my google drive. 

In [ ]:
!cp test_spec.zip /content/gdrive/MyDrive/SpeechRecognition

Commit all the changes done in the colab. 

In [ ]:
drive.flush_and_unmount() 

#Mel Spectogram Images

In [ ]:
def mel_spectogram_test(examples):
  hop_length = 512 
  n_fft = 512 
  os.makedirs('test_mel_spec', exist_ok = True)
  spec_images = '/content/test_mel_spec'

  for idx,ex in enumerate(examples): 
    if idx%1000 == 0: print(idx)
    fig = plt.Figure()
    canvas = FigureCanvas(fig)
    ax = fig.add_subplot(111)
    
    name = re.findall(r'[\w]+.wav',ex)[0]
    clip, sample_rate = librosa.load(ex)
    
    fmax = sample_rate/2

    spect = librosa.feature.melspectrogram(clip,sr= sample_rate, n_fft = n_fft, hop_length = hop_length)
    img = librosa.display.specshow(librosa.power_to_db(spect, ref=np.max), y_axis=None, x_axis=None,fmax = fmax, ax=ax)

    fig.savefig(f'{spec_images}/{name[:-3]}jpg')

mel_spectogram_test(examples)

0
1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000
92000
93000
94000
95000
96000
97000
98000
99000
100000
101000
102000
103000
104000
105000
106000
107000
108000
109000
110000
111000
112000
113000
114000
115000
116000
117000
118000
119000
120000
121000
122000
123000
124000
125000
126000
127000
128000
129000
130000
131000
132000
133000
134000
135000
136000
137000
138000
139000
140000
141000
142000
143000
144000
145000
146000
147000
148000
149000
150000
151000
152000
153000
154000
155000
156000
157000
158000


In [ ]:
%%bash 
zip -r /content/test_mel.zip /content/test_mel_spec

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



##Upload 
Upload the `test_spec` images to my google drive. 

In [ ]:
!cp test_mel.zip /content/drive/MyDrive/SpeechRecognition

Commit all the changes done in the colab. 

In [ ]:
drive.flush_and_unmount()

#MFCC Images

In [ ]:
def mfcc_test(examples):
  hop_length = 512
  n_fft = 512
  os.makedirs('test_mfcc_spec', exist_ok = True)
  spec_images = '/content/test_mel_spec'

  for idx,ex in enumerate(examples): 
    if idx%1000 == 0: print(idx)
    fig = plt.Figure()
    canvas = FigureCanvas(fig)
    ax = fig.add_subplot(111)
    
    name = re.findall(r'[\w]+.wav',ex)[0]
    clip, sample_rate = librosa.load(ex)
    
    fmax = sample_rate/2

    mfccs = librosa.feature.mfcc(clip,sr= sample_rate, n_fft = n_fft, n_mfcc = 50, hop_length = hop_length, dct_type = 1)
    img = librosa.display.specshow(mfccs,y_axis=None, x_axis=None,fmax = fmax, ax=ax)
    
    fig.savefig(f'{spec_images}/{name[:-3]}jpg')

mfcc_test(examples)

0
1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000
92000
93000
94000
95000
96000
97000
98000
99000
100000
101000
102000
103000
104000
105000
106000
107000
108000
109000
110000
111000
112000
113000
114000
115000
116000
117000
118000
119000
120000
121000
122000
123000
124000
125000
126000
127000
128000
129000
130000
131000
132000
133000
134000
135000
136000
137000
138000
139000
140000
141000
142000
143000
144000
145000
146000
147000
148000
149000
150000
151000
152000
153000
154000
155000
156000
157000
158000


In [ ]:
!zip -r /content/mfcc.zip /content/test_mel_spec

Streaming output truncated to the last 5000 lines.
  adding: content/test_mel_spec/clip_ad0126600.jpg (deflated 13%)
  adding: content/test_mel_spec/clip_3d7feea7b.jpg (deflated 17%)
  adding: content/test_mel_spec/clip_24aa15dd9.jpg (deflated 15%)
  adding: content/test_mel_spec/clip_93f16e64f.jpg (deflated 10%)
  adding: content/test_mel_spec/clip_fa6edc339.jpg (deflated 10%)
  adding: content/test_mel_spec/clip_41e41c2ac.jpg (deflated 11%)
  adding: content/test_mel_spec/clip_4a227f3e2.jpg (deflated 7%)
  adding: content/test_mel_spec/clip_a24bbb2c4.jpg (deflated 8%)
  adding: content/test_mel_spec/clip_c68205ec4.jpg (deflated 21%)
  adding: content/test_mel_spec/clip_20b42dd0a.jpg (deflated 8%)
  adding: content/test_mel_spec/clip_95198f9cc.jpg (deflated 7%)
  adding: content/test_mel_spec/clip_7801d1a6d.jpg (deflated 11%)
  adding: content/test_mel_spec/clip_b37b034a9.jpg (deflated 74%)
  adding: content/test_mel_spec/clip_151372c4f.jpg (deflated 8%)
  adding: content/test_mel_spe

##Upload 
Upload the `test_spec` images to my google drive. 

In [ ]:
!cp -r mfcc.zip /content/drive/MyDrive

Commit all the changes done in the colab. 

In [ ]:
drive.flush_and_unmount()